![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 15. <i>Korekta gramatyczna</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Ostatnią z omawianych przez nas technik stosowaną podczas wspomagania tłumaczenia jest korekta gramatyczna. Automatyczna korekta gramatyczna tekstu to ambitne zadanie odnalezienia możliwych błędów niezwiązanych bezpośrednio z pisownią. Są to między innymi:
* błędy gramatyczne
* źle użyte słowa
* złe połączenia wyrazowe
* błędy interpunkcyjne
* kolokwializmy
* redundancja (np. "tylko i wyłącznie")

Warto zwrócić uwagę, iż systemy do korekcji gramatycznej można traktować jako klasyfikatory binarne. Przyjmijmy, że odpowiedź pozytywna korektora to wykrycie błędu w tekście, natomiast negatywna - brak błędu. Wówczas rozróżniamy dwa typy pomyłek: false positive oraz false negative. False positive to tzw. "fałszywy alarm" - zbyt duża ich ilość spowoduje wydłużenie czasu pracy użytkownika przez konieczność analizowania zgłoszeń, które w istocie błędami nie są. Co jednak jeszcze gorsze, zbyt duża ilość false positives powoduje spadek zaufania użytkownika do systemu oraz drastyczny spadek satysfakcji z używania systemu. Te drugie błędy - false negatives - to z kolei faktyczne błędy w tekście, które nie zostały wyłapane przez system korekty. Stare polskie porzekadło głosi, że "czego oko nie widzi, tego sercu nie żal". Niestety jednak problem pojawia się, kiedy dostrzeże to jakieś inne oko... Wysoka liczba false negatives wprawdzie skraca czas korekty (sic!), ale odbywa się to kosztem jakości całego procesu. Idealnie zatem byłoby zminimalizować zarówno liczbę false positives, jak i false negatives. Jak jednak łatwo się domyślić, nie jest to zawsze możliwe. Korektor gramatyczny, który jest bardzo restrykcyjny i raportuje wiele błędów, będzie miał tendencję do popełniania false positives. Natomiast korektor bardziej pobłażliwy niechybnie popełni wiele false negatives. Co zatem jest ważniejsze? Praktyka wskazuje, że oba parametry mają podobną wagę, ale jednak odrobinę ważniejsze jest powstrzymanie się od false positives.

Do najbardziej popularnych narzędzi wspomagających korektę gramatyczną tekstu należą Grammarly oraz LanguageTool. Na dzisiejszych zajęciach zajmiemy się tym drugim. LanguageTool został pierwotnie napisany jako praca dyplomowa Daniela Nabera, a następnie intensywnie rozwijany wspólnie z Marcinem Miłkowskim. Aż do dziś projekt jest ciągle rozwijany, zwiększana jest liczba obsługiwanych języków oraz dokładność działania.

LanguageTool jest systemem opartym na regułach. W dobie wszechobecnej sztucznej inteligencji opartej na uczeniu maszynowym rozwiązanie to wydaje się nieco przestarzałe. Jednak to właśnie reguły stanowią o sile LanguageToola - pozwalają one na zwiększenie precyzji korektora poprzez minimalizację false positives. Warto wspomnieć, iż liczne reguły LanguageToola dotyczą również korekty pisowni. Czyni to z LanguageToola kompletne narzędzie do korekty tekstu. Polecam przejrzenie zestawu reguł LanguageToola dla języka angielskiego: https://community.languagetool.org/rule/list?lang=en

Czas uruchomić to narzędzie. Skorzystajmy z Pythona.

Następnie możemy użyć LanguageToola w programie Pythonowym: (przykład zaczerpnięty z oficjalnego tutoriala: https://pypi.org/project/language-tool-python/)

In [3]:
import language_tool_python
import pprint
tool = language_tool_python.LanguageTool('en-US') 

text = 'A sentence with a error in the Hitchhiker’s Guide tot he Galaxy'

pp = pprint.PrettyPrinter(depth=2)
errors = tool.check(text)
pp.pprint(errors)

[Match({'ruleId': 'EN_A_VS_AN', 'message': 'Use “an” instead of ‘a’ if the following word starts with a vowel sound, e.g. ‘an article’, ‘an hour’.', 'replacements': ['an'], 'offsetInContext': 16, 'context': 'A sentence with a error in the Hitchhiker’s Guide tot he ...', 'offset': 16, 'errorLength': 1, 'category': 'MISC', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"}),
 Match({'ruleId': 'TOT_HE', 'message': 'Did you mean “to the”?', 'replacements': ['to the'], 'offsetInContext': 43, 'context': '... with a error in the Hitchhiker’s Guide tot he Galaxy', 'offset': 50, 'errorLength': 6, 'category': 'TYPOS', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"})]


Przeanalizujmy format zwracanego wyniku. Otrzymujemy listę obiektów Match - zawiadomień o potencjalnym błędzie. Razem z każdym błędem otrzymujemy m.in. identyfikator użytej reguły, opis błędu, rekomendancję poprawy, kontekst.

### Ćwiczenie 1: Użyj LanguageTool do znalezienia jak największej liczby prawdziwych błędów na swoim ulubionym portalu internetowym. Skorzystaj z poznanych wcześniej technik web scrapingu. Uwaga - LanguageTool najprawdopodobniej oznaczy nazwy własne jako literówki - ten typ błędu nie powinien być brany pod uwagę.

In [4]:
import requests
from bs4 import BeautifulSoup


def find_errors(website_url):
    page = requests.get(website_url)
    soup = BeautifulSoup(page.content, 'html.parser')
    tool = language_tool_python.LanguageTool('pl-PL')
    for script in soup(["script", "style"]):
        script.extract()
    text = " ".join(soup.text.split())
    result = []
    for error in tool.check(text):
        if error.ruleId != 'MORFOLOGIK_RULE_PL_PL':
            result.append(error)

    return result

In [5]:
print(find_errors('https://wmi.amu.edu.pl/'))

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "treśćprzejdź"?', 'replacements': ['treśćprzejdź'], 'offsetInContext': 43, 'context': '...rzeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPr...', 'offset': 261, 'errorLength': 12, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': 'Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPrzejdź do Dostępność A A A en pl Wyszukaj Wyszukaj Nawigacja mobilna Wydział - Wydział Matematyki i Informatyki Wydział - Wydział Matematyki i Informatyki NO XML TR1A Wydział Pokaż menu szczegółowe Powrót do głównego menu O wydziale Władze wydziału Struktura wydziału Rada Naukowa Dyscyplin Rady programowe Pracownicy Projekty Historia Biblioteka wydziałowa Informator WMI w mediach Wybory 2024 Kontakt Życie naukowe Pokaż m

### Ćwiczenie 2: Napisz skrypt, który poszuka błędów w komentarzach klasy Javowej (zwykłych // oraz w javadocach). Uruchom ten skrypt na źródłach wybranego opensourcowego projektu w Javie.

In [8]:
def correct_java_grammar(java_file_path):
    import re

    def sanitize(text: str) -> str:
        text = re.sub(r'\s+', ' ', text)
        text = re.sub(r'/|\{|}|\*|\[|]|(@\w+)', '', text)

        return text

    text = ""
    result = []
    tool = language_tool_python.LanguageTool('en-US')
    with open(java_file_path, 'r') as file:
        text = file.read()
    lines = re.findall(r'//.+\n', text) + re.findall(r'\*.+\n', text)
    text = ' '.join(lines)
    for error in tool.check(sanitize(text)):
        if error.ruleId != 'MORFOLOGIK_RULE_EN_US':
            result.append(error)

    return result

In [9]:
print(correct_java_grammar('test.java'))

[Match({'ruleId': 'UPPERCASE_SENTENCE_START', 'message': 'This sentence does not start with an uppercase letter.', 'replacements': ['Index'], 'offsetInContext': 33, 'context': 'neo4j.com www.gnu.orglicenses>.  index into the buffer character array to read...', 'offset': 33, 'errorLength': 5, 'category': 'CASING', 'ruleIssueType': 'typographical', 'sentence': "index into the buffer character array to read the next time nextChar() is called  last index (effectively length) of characters in use in the buffer  bufferPos denoting the start of this current line that we're reading  bufferPos when we started reading the current field  1-based value of which logical line we're reading a.t.m."}), Match({'ruleId': 'CONSECUTIVE_SPACES', 'message': 'It seems like there are too many consecutive spaces here.', 'replacements': [' '], 'offsetInContext': 43, 'context': '... read the next time nextChar() is called  last index (effectively length) of chara...', 'offset': 113, 'errorLength': 2, 'category':

https://github.com/neo4j/neo4j/blob/5.20/community/csv/src/main/java/org/neo4j/csv/reader/BufferedCharSeeker.java